In [21]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
from geodatasets import get_path
import numpy as np
import re
from math import radians, sin, cos, sqrt, atan2
from shapely.geometry import Point
from scipy.spatial import cKDTree
import folium
from tower_ping_search import process_pings

**Data processing overview**

- What data were we given?
- What data did we source?
- How did we process these data sets?
- Our RAG implementation
- Web App

Data Given:
- Tower ping logs
- Tallest buildings in San Francisco

Data Sourced:
- San Francisco shoreline Geographical data
- Existing Commercial Telecomm infrastructure
- Proposed Commercial Telecomm infrastructure

In [2]:
tallest_buildings_df = pd.read_csv('C:/Users/alan1/Documents/Projects/rtx_hackathon_2024/B_GIS/data/map_data/Tallest_Towers.csv')
tallest_buildings_df.head()

Rank                   Name Height ft(m)  Floors                  Use   
0     1       Salesforce Tower  1,070 (326)      61               Office  \
1     2   Transamerica Pyramid    853 (260)      48               Office   
2     3            181 Fremont    803 (245)      56  Office, Residential   
3     4  555 California Street    779 (237)      52               Office   
4     5   2700 Sloat Boulevard    735 (224)      50          Residential   

   Year                   Coordinates  Latitude  Longitude  
0  2018          37.7899°N 122.3969°W  37.78990 -122.39690  
1  1972  37°47′42.72″N 122°24′10.08″W  37.79520 -122.40280  
2  2017        37.78970°N 122.39535°W  37.78970 -122.39535  
3  1969  37°47′30.84″N 122°24′13.68″W  37.79100 -122.40380  
4  2024  37°73′59.75″N 122°50′36.22″W  37.73591 -122.50360

In [3]:
sf_towers_proposed_df = pd.read_csv('C:/Users/alan1/Documents/Projects/rtx_hackathon_2024/B_GIS/data/map_data/Proposed_Commercial_Wireless_Telecommunication_Services_Facilities_in_San_Francisco_20240712.csv')
sf_towers_proposed_df.head()

Carrier        ID             Address         Search Ring Name ID Block   
0    AT&T  CCL01402         201 Mission  SF Transbay Transit Center  3718  \
1    AT&T  CCL02220      333 Fremont St              333 Fremont St   TBD   
2    AT&T  CCL02265  350 Sansome Street          California & Front   TBD   
3    AT&T  CCL03272    3301 Lyon Street                         TBD   TBD   
4    AT&T  CCL03293  1201 Fourth Street                 Anza Street  8711   

   Lot Zoning District Height and Bulk District Type of Building   
0  026       C-3-O(SF)                    400-S       Commercial  \
1  TBD             TBD                      TBD              TBD   
2  TBD             TBD                      TBD              TBD   
3  TBD             TBD                      TBD              TBD   
4  028           MB-RA                    MB-RA              TBD   

   Preference (1-7)  ... Location of BTS Type of Technology   
0               NaN  ...             TBD            LTE, 5G  \
1               NaN  ...             TBD            LTE, 5G   
2               NaN  ...             TBD            LTE, 5G   
3               NaN  ...             TBD            LTE, 5G   
4               NaN  ...             TBD            LTE, 5G   

  Radio Frequency Range (Megahertz) Power Output of Equipment   
0          700, 850, 1900,1700,2300                       TBD  \
1          700, 850, 1900,1700,2300                       TBD   
2          700, 850, 1900,1700,2300                       TBD   
3          700, 850, 1900,1700,2300                       TBD   
4          700, 850, 1900,1700,2300                       TBD   

  Height to Top of Antenna Name of Community Liason   
0                      NaN         Melissa Murphree  \
1                      NaN         Melissa Murphree   
2                      NaN         Melissa Murphree   
3                      NaN         Melissa Murphree   
4                      NaN         Melissa Murphree   

  Phone Number of Community Liason  Comments        LAT        LONG  
0                     925-963-8027       NaN  37.791034 -122.394768  
1                     925-963-8027       NaN  37.787682 -122.392695  
2                     925-963-8027       NaN  37.793783 -122.401001  
3                     925-963-8027       NaN  37.801884 -122.448296  
4                     925-963-8027       NaN  37.772693 -122.391128  

[5 rows x 23 columns]

In [4]:
sf_towers_old_df = pd.read_csv('C:/Users/alan1/Documents/Projects/rtx_hackathon_2024/B_GIS/data/map_data/Existing_Commercial_Wireless_Telecommunication_Services_Facilities_in_San_Francisco_20240712.csv')
sf_towers_old_df.head()

Carrier       ID  Search Ring Name ID Block      Lot Zoning District   
0    AT&T  CCL00001       Marshall Hale  1017      028            RM-2  \
1    AT&T  CCL00002         Embarcadero  0237  014/016           C-3-O   
2    AT&T  CCL00005   Mercy High School  7231      003         RH-1(D)   
3    AT&T  CCL00006      Bernal Heights  3637      069             NCT   
4    AT&T  CCL00049      Marina Safeway  0503      030            RC-3   

  Hight and Bulk District Type of Building  Preference (1-7)   
0                    80-E       Commercial               NaN  \
1                   350-S       Commercial               NaN   
2                    40-X           Public               NaN   
3               40-X/65-B       Commercial               NaN   
4               65-A/40-X       Commercial               NaN   

  Type of Consumer Services  ... Location of BTS Type of Technology   
0       voice, video & data  ...        Basement          UMTS, LTE  \
1       voice, video & data  ...        Basement          UMTS, LTE   
2       voice, video & data  ...       Ground Fl      UMTS, LTE, 5G   
3       voice, video & data  ...       Ground Fl          UMTS, LTE   
4       voice, video & data  ...        Basement          UMTS, LTE   

  Radio Frequency Range (Megahertz) Power Output of Equipment (Watts)   
0          700, 850, 1900,1700,2300                             16650  \
1          700, 850, 1900,1700,2300                             16650   
2          700, 850, 1900,1700,2300                             16650   
3          700, 850, 1900,1700,2300                             16650   
4          700, 850, 1900,1700,2300                              7182   

  Height to Top of Antenna Name of Community Liason   
0                       87         Melissa Murphree  \
1                      252         Melissa Murphree   
2                       67         Melissa Murphree   
3                      120         Melissa Murphree   
4                      127         Melissa Murphree   

  Phone Number of Community Liason   
0                     925-963-8027  \
1                     925-963-8027   
2                     925-963-8027   
3                     925-963-8027   
4                     925-963-8027   

                                          Comments  Latitude  Longitude  
0  CCL02745 is a proposed replacement for CCL00001  37.78688 -122.45489  
1                                              NaN  37.79398 -122.39962  
2                                              NaN  37.72981 -122.47384  
3                                              NaN  37.75522 -122.41836  
4                                              NaN  37.80087 -122.42503  

[5 rows x 22 columns]

In [5]:
# Get high-risk zones for liquefaction
sf_hazard_zones_df = gpd.read_file('C:/Users/alan1/Documents/Projects/rtx_hackathon_2024/B_GIS/data/map_data/San_Francisco_Seismic_Hazard_Zones_20240712.csv')
sf_hazard_zones_df["the_geom"] = gpd.GeoSeries.from_wkt(sf_hazard_zones_df["the_geom"])
sf_hazard_zones_df.head()

the_geom   ID
0  MULTIPOLYGON (((-122.50968 37.74962, -122.5097...  308
1  MULTIPOLYGON (((-122.49905 37.71731, -122.4992...  309
2  MULTIPOLYGON (((-122.49621 37.72397, -122.4960...  310
3  MULTIPOLYGON (((-122.49504 37.72857, -122.4944...  311
4  MULTIPOLYGON (((-122.49374 37.72617, -122.4936...  312

In [6]:
# Get shore coordinates
sf_shore_coords_df = gpd.read_file('C:/Users/alan1/Documents/Projects/rtx_hackathon_2024/B_GIS/data/map_data/SF_Shoreline_and_Islands_20240712.csv')
sf_shore_coords_df["the_geom"] = gpd.GeoSeries.from_wkt(sf_shore_coords_df["the_geom"])
sf_shore_coords_df.head()

SDE_SFGIS_ PERIMETER                                           the_geom   
0          0         0  MULTIPOLYGON (((-122.42488 37.8108, -122.42485...  \

  OBJECTID INNERWATER SHAPE__ARE SHAPE__LEN  
0        1                     0          0

In [10]:
tower_ping_df = process_pings()
tower_ping_df.head()

Carrier Type of Building Type of Consumer Services Number of Antennas   
0  Tmobile     Utility Pole        voice, video, data                  1  \
1  Tmobile     Utility Pole        voice, video, data                  1   
2  Tmobile     Utility Pole        voice, video, data                  1   
3  Tmobile     Utility Pole        voice, video, data                  1   
4  Tmobile     Utility Pole        voice, video, data                  1   

  Radio Frequency Range (Megahertz)   Latitude   Longitude  
0                       1900 / 2100  37.777024 -122.508037  
1                       1900 / 2100  37.749500 -122.508000  
2                       1900 / 2100  37.778500 -122.497000  
3                       1900 / 2100  37.760233 -122.504958  
4                       1900 / 2100  37.753500 -122.425000

In [13]:
# Shoreline geometry
shoreline_geometry = sf_shore_coords_df["the_geom"].iloc[0]
# Extract shoreline points
points = [coord for polygon in shoreline_geometry.geoms for coord in polygon.exterior.coords]
# Create GeoDataFrame for shoreline points
shoreline_gdf = gpd.GeoDataFrame(geometry=[Point(p) for p in points])
# Build a KD-tree from shoreline points
kdtree = cKDTree(shoreline_gdf.geometry.apply(lambda x: (x.x, x.y)).tolist())
# Find the nearest shoreline point for each building
tallest_buildings_df["Nearest_Shoreline_Index"] = tallest_buildings_df.apply(
    lambda row: kdtree.query([row["Longitude"], row["Latitude"]])[1],
    axis=1,
)
# Extract the nearest shoreline point coordinates
tallest_buildings_df["Nearest_Shoreline_Latitude"] = tallest_buildings_df.apply(
    lambda row: shoreline_gdf.geometry.iloc[row["Nearest_Shoreline_Index"]].y,
    axis=1,
)
tallest_buildings_df["Nearest_Shoreline_Longitude"] = tallest_buildings_df.apply(
    lambda row: shoreline_gdf.geometry.iloc[row["Nearest_Shoreline_Index"]].x,
    axis=1,
)

# Calculate distance to shoreline using Haversine formula (in miles)

def haversine(lat1, lon1, lat2, lon2):
    '''Haversine formula determines the distance between two points on a sphere 
    given their longitudes and latitudes.
    '''
    R = 6371  # Earth radius in km
    dlat = radians(lat2 - lat1)
    dlon = radians(lon2 - lon1)
    a = sin(dlat / 2) ** 2 + cos(radians(lat1)) * cos(radians(lat2)) * sin(dlon / 2) ** 2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    distance_km = R * c
    distance_miles = distance_km * 0.621371  # Convert km to miles
    return distance_miles

tallest_buildings_df["Distance_to_Shore"] = tallest_buildings_df.apply(
    lambda row: haversine(
        row["Latitude"],
        row["Longitude"],
        row["Nearest_Shoreline_Latitude"],
        row["Nearest_Shoreline_Longitude"],
    ),
    axis=1,
)

# Display relevant columns
tallest_buildings_df.head()

Rank                   Name Height ft(m)  Floors                  Use   
0     1       Salesforce Tower  1,070 (326)      61               Office  \
1     2   Transamerica Pyramid    853 (260)      48               Office   
2     3            181 Fremont    803 (245)      56  Office, Residential   
3     4  555 California Street    779 (237)      52               Office   
4     5   2700 Sloat Boulevard    735 (224)      50          Residential   

   Year                   Coordinates  Latitude  Longitude   
0  2018          37.7899°N 122.3969°W  37.78990 -122.39690  \
1  1972  37°47′42.72″N 122°24′10.08″W  37.79520 -122.40280   
2  2017        37.78970°N 122.39535°W  37.78970 -122.39535   
3  1969  37°47′30.84″N 122°24′13.68″W  37.79100 -122.40380   
4  2024  37°73′59.75″N 122°50′36.22″W  37.73591 -122.50360   

   Nearest_Shoreline_Index  Nearest_Shoreline_Latitude   
0                     5548                   37.793429  \
1                     4867                   37.799842   
2                     5548                   37.793429   
3                     5094                   37.797871   
4                    29909                   37.734816   

   Nearest_Shoreline_Longitude  Distance_to_Shore  
0                  -122.391724           0.373266  
1                  -122.397642           0.426788  
2                  -122.391724           0.324933  
3                  -122.395861           0.642860  
4                  -122.508272           0.266273

In [14]:
# Find nearst towers to each building

# Initialize an empty column for distances
tallest_buildings_df["Distance_to_Tower"] = None
tallest_buildings_df["Tower_Latitude"] = None
tallest_buildings_df["Tower_Longitude"] = None

# Set the maximum distance threshold (0.5 miles)
max_distance_miles = 0.5

# Iterate over each building
for index, building_row in tallest_buildings_df.iterrows():
    building_lat = building_row["Latitude"]
    building_lon = building_row["Longitude"]
    
    # Initialize lists to store distances and tower coordinates
    distances_to_towers = []
    tower_latitudes = []
    tower_longitudes = []
    
    # Calculate distances to each tower
    for tower_index, tower_row in tower_ping_df.iterrows():
        tower_lat = tower_row["Latitude"]
        tower_lon = tower_row["Longitude"]
        
        # Calculate distance
        distance = haversine(building_lat, building_lon, tower_lat, tower_lon)
        
        # Check if the distance is within the threshold
        if distance <= max_distance_miles:
            distances_to_towers.append(distance)
            tower_latitudes.append(tower_lat)
            tower_longitudes.append(tower_lon)
    
    # Store the lists of distances and tower coordinates in the DataFrame
    tallest_buildings_df.at[index, "Distance_to_Tower"] = distances_to_towers
    tallest_buildings_df.at[index, "Tower_Latitude"] = tower_latitudes
    tallest_buildings_df.at[index, "Tower_Longitude"] = tower_longitudes

# Display relevant columns
tallest_buildings_df.head()

Rank                   Name Height ft(m)  Floors                  Use   
0     1       Salesforce Tower  1,070 (326)      61               Office  \
1     2   Transamerica Pyramid    853 (260)      48               Office   
2     3            181 Fremont    803 (245)      56  Office, Residential   
3     4  555 California Street    779 (237)      52               Office   
4     5   2700 Sloat Boulevard    735 (224)      50          Residential   

   Year                   Coordinates  Latitude  Longitude   
0  2018          37.7899°N 122.3969°W  37.78990 -122.39690  \
1  1972  37°47′42.72″N 122°24′10.08″W  37.79520 -122.40280   
2  2017        37.78970°N 122.39535°W  37.78970 -122.39535   
3  1969  37°47′30.84″N 122°24′13.68″W  37.79100 -122.40380   
4  2024  37°73′59.75″N 122°50′36.22″W  37.73591 -122.50360   

   Nearest_Shoreline_Index  Nearest_Shoreline_Latitude   
0                     5548                   37.793429  \
1                     4867                   37.799842   
2                     5548                   37.793429   
3                     5094                   37.797871   
4                    29909                   37.734816   

   Nearest_Shoreline_Longitude  Distance_to_Shore   
0                  -122.391724           0.373266  \
1                  -122.397642           0.426788   
2                  -122.391724           0.324933   
3                  -122.395861           0.642860   
4                  -122.508272           0.266273   

                                   Distance_to_Tower   
0  [0.3765703908767611, 0.4185534604676551, 0.423...  \
1  [0.4496203926611257, 0.4549756429879831, 0.436...   
2  [0.444608501737584, 0.48455287593541196, 0.373...   
3  [0.4652003965592039, 0.25515679943241715, 0.28...   
4          [0.1425836204584958, 0.49843685992852577]   

                                      Tower_Latitude   
0  [37.79411, 37.79471, 37.79264, 37.79324, 37.79...  \
1  [37.7946, 37.7996, 37.799456, 37.79411, 37.794...   
2  [37.79411, 37.79471, 37.79324, 37.79377, 37.79...   
3  [37.7946, 37.79411, 37.79471, 37.79264, 37.793...   
4                             [37.7351, 37.74223889]   

                                     Tower_Longitude  
0  [-122.40128, -122.40156, -122.40384, -122.4005...  
1  [-122.411, -122.409, -122.408706, -122.40128, ...  
2  [-122.40128, -122.40156, -122.40053, -122.4000...  
3  [-122.411, -122.40128, -122.40156, -122.40384,...  
4                            [-122.506, -122.499222]

In [ ]:
# large_given_lat = tower_ping_df["Latitude"].tolist()
# large_given_lon = tower_ping_df["Longitude"].tolist()
# coordinates = [[lat, lon] for lat, lon in zip(large_given_lat,large_given_lon)]

# new_coordinates = []

# for index,buildings in enumerate(tallest_buildings_df["Name"]):
#     near_building_towers_lat = tallest_buildings_df.at[index, "Tower_Latitude"]
#     near_building_towers_lon = tallest_buildings_df.at[index, "Tower_Longitude"]
#     for ind, lat_val in enumerate(near_building_towers_lat):
#         print(ind)
#         individual_tower_lat = near_building_towers_lat[ind]
#         individual_tower_lon = near_building_towers_lon[ind]
#         coord_query = [individual_tower_lat,individual_tower_lon]
#         if coord_query in coordinates:
#             new_coordinates.append(coord_query)

In [22]:
# Filter based on call information
building = 'Office'
min_floors = 40
dist_to_shore = 0.2
checked_df = pd.DataFrame(tallest_buildings_df[(tallest_buildings_df['Use'].apply(lambda x: building in x if isinstance(x, str) else any(building in item for item in x))) & (tallest_buildings_df['Floors'] >= min_floors) & (tallest_buildings_df['Distance_to_Shore'] <= dist_to_shore)])
#checked_df = pd.DataFrame(towers_df[(towers_df['Use'].apply(lambda x: building not in x if isinstance(x, str) else any(building not in item for item in x))) & (towers_df['Floors'] >= min_floors)])

checked_df.head()

Rank                             Name Height ft(m)  Floors     Use  Year   
12    13          Four Embarcadero Center    571 (174)      45  Office  1982  \
15    16  Spear Tower at One Market Plaza    564 (172)      43  Office  1976   

                     Coordinates  Latitude  Longitude   
12  37°47′42.72″N 122°23′45.96″W   37.7952  -122.3961  \
15  37°47′35.84″N 122°23′40.27″W   37.7933  -122.3945   

    Nearest_Shoreline_Index  Nearest_Shoreline_Latitude   
12                     5510                   37.796582  \
15                     5546                   37.793872   

    Nearest_Shoreline_Longitude  Distance_to_Shore   
12                  -122.394681           0.122934  \
15                  -122.391982           0.143052   

                                    Distance_to_Tower   
12  [0.2926751665722561, 0.3000222165717927, 0.458...  \
15  [0.37438835703159545, 0.39758828929072165, 0.3...   

                                       Tower_Latitude   
12  [37.79411, 37.79471, 37.79264, 37.79324, 37.79...  \
15  [37.79411, 37.79471, 37.79324, 37.79377, 37.79...   

                                      Tower_Longitude  
12  [-122.40128, -122.40156, -122.40384, -122.4005...  
15  [-122.40128, -122.40156, -122.40053, -122.4000...

In [20]:
# Initialize map around San Francisco
sf_map = folium.Map(location=[37.7750, -122.4200], zoom_start=12, max_zoom=16)

In [15]:
# Display Building and "Safety Range" on map
for idx, row in tallest_buildings_df.iterrows():
    distance = round(row['Distance_to_Shore'], 3)
    icon_color = 'black'
    if distance < 0.2:
        icon_color = 'red'
    elif 0.2 <= distance < 0.5:
        icon_color = 'orange'
    else:
        icon_color = 'green'
    
    # Customize the popup content with HTML
    popup_content = f"<h4>{row['Name']} Building Info</h4>" \
                    f"<p><strong>Height:</strong> {row['Height ft(m)']} ft(m)</p>" \
                    f"<p><strong>Floors:</strong> {row['Floors']}</p>" \
                    f"<p><strong>Distance to Shore:</strong> {row['Distance_to_Shore']}</p>" \
                    f"<p><strong>Building Type:</strong> {row['Use']}</p>"

    # Create a popup with custom width
    popup = folium.Popup(popup_content, min_width=300, max_width=500)

    # Add a marker with the popup and tooltip to the map
    folium.Marker(
        location=[row['Latitude'], row['Longitude']],
        tooltip=f"{row['Name']} CLICK FOR MORE INFO",
        popup=popup,
        icon=folium.Icon(color=icon_color, icon='building', prefix='fa')
    ).add_to(sf_map)

# Save the map (optional)
# sf_map.save('data/sf_towers_map.html')

# Display the map
sf_map


In [ ]:
# from folium.plugins import HeatMap
# # Create a heat map for ping datapoints

# #m = folium.Map(location=[37.7749, -122.4194], zoom_start=12)

# selected_columns = ['Latitude','Longitude']
# call_location_df = tower_ping_df[selected_columns]

# # Add the heatmap layer
# heatmap_layer = HeatMap(call_location_df).add_to(sf_map)

# sf_map

In [23]:
# Display high-risk zones
for idx, row in sf_hazard_zones_df.iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    sim_geo = gpd.GeoSeries(row["the_geom"]).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "red"})
    folium.Popup(row["ID"]).add_to(geo_j)
    geo_j.add_to(sf_map)

sf_map

In [27]:
# Display proposed cell towers
for idx, row in sf_towers_proposed_df.iterrows():
    if not np.isnan(row['LAT']) and not np.isnan(row['LONG']):
        folium.Marker(
            location=[row['LAT'], row['LONG']],
            tooltip=row['Carrier'],
            popup=row['Carrier'],
            icon=folium.Icon(color='red', icon='tower-cell', prefix='fa')
        ).add_to(sf_map)

sf_map

In [ ]:
# Display cell towers
for idx, row in sf_towers_old_df.iterrows():
    if not np.isnan(row['Latitude']) and not np.isnan(row['Longitude']):
        folium.Marker(
            location=[row['Latitude'], row['Longitude']],
            tooltip=row['Carrier'],
            popup=row['Carrier'],
            icon=folium.Icon(color='green', icon='tower-cell', prefix='fa')
        ).add_to(sf_map)

sf_map